In [1]:
import json
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from pathlib import Path
from itertools import zip_longest
import os
import glob

In [2]:
# data = json.load(open("2025-06-15_11-38-56-781937_measure_weight_FORCE_MEASUREMENT_CASE1.json", encoding="utf-8"))
data = json.load(open("2025-06-15_11-39-04-387039_measure_weight_FORCE_MEASUREMENT_CASE.json", encoding="utf-8"))

df = pd.json_normalize(
    data,
    record_path="raw_measurements",
    meta=["version","type","start_time","end_time","sampling_rate","weight_filter","zero_offset","expected_weight","robot_type","force_sensor_offset"],
    errors="ignore"
)
df['timestamp'] = df['timestamp'] - df['timestamp'][0]
print(df.shape)
print(df.keys())
print(df.head())

(493, 19)
Index(['timestamp', 'value', 'force_vector', 'robot_tcp.timestamp',
       'robot_tcp.flange', 'robot_tcp.tcp_offset', 'robot_tcp.velocity_linear',
       'robot_tcp.velocity_angular', 'robot_tcp.joint_angles', 'version',
       'type', 'start_time', 'end_time', 'sampling_rate', 'weight_filter',
       'zero_offset', 'expected_weight', 'robot_type', 'force_sensor_offset'],
      dtype='object')
   timestamp  value          force_vector  robot_tcp.timestamp  \
0   0.000000 -0.054   [0.603, 0.618, 9.0]         1.749980e+09   
1   0.001043 -0.055    [0.647, 0.59, 9.0]         1.749980e+09   
2   0.002042 -0.055   [0.683, 0.56, 10.0]         1.749980e+09   
3   0.003042 -0.055  [0.711, 0.529, 11.0]         1.749980e+09   
4   0.004042 -0.055   [0.73, 0.502, 11.0]         1.749980e+09   

                                    robot_tcp.flange  \
0  [[-0.5583840012550354, -0.3735954165458679, -0...   
1  [[-0.5583451986312866, -0.37359368801116943, -...   
2  [[-0.5583451986312866, -

In [3]:
input_folder = "all measurements"
output_folder = "All measurements, cleaned"

# make sure output folder exists
os.makedirs(output_folder, exist_ok=True)

files = glob.glob(os.path.join(input_folder, "*.json"))

for file in files:
    print(f"\nProcessing: {file}")
    
    try:
        # load JSON
        with open(file, encoding="utf-8") as f:
            data = json.load(f)

        # flatten JSON into dataframe
        df = pd.json_normalize(
            data,
            record_path="raw_measurements",
            meta=["version","type","start_time","end_time","sampling_rate","weight_filter","zero_offset","expected_weight","robot_type","force_sensor_offset"],
            errors="ignore"
        )

        df['timestamp'] = df['timestamp'] - df['timestamp'].iloc[0]

        # check if it fulfills all requirements
        if len(df) < 400:
            print(f"⚠️ Skipping {file} — only {len(df)} rows")
            continue
            
        if "value" not in df.columns:
            print(f"⚠️ Skipping {file} — no 'value' column")
            continue

        if df['value'].isna().all() or (df['value'] == 0).all():
            print(f"⚠️ Skipping {file} — all values are 0 or NaN")
            continue

        # save cleaned file
        base_name = os.path.basename(file)
        save_path = os.path.join(output_folder, base_name.replace(".json", "_cleaned.csv"))
        df.to_csv(save_path, index=False, encoding="utf-8")
        print(f"✅ Saved cleaned file to {save_path}")

    except Exception as e:
        print(f"⚠️ Skipping file {file}, error: {e}")
        continue



Processing: all measurements\2025-06-15_11-44-34-096154_measure_weight_FORCE_MEASUREMENT_CASE.json
✅ Saved cleaned file to All measurements, cleaned\2025-06-15_11-44-34-096154_measure_weight_FORCE_MEASUREMENT_CASE_cleaned.csv

Processing: all measurements\2025-06-15_11-44-43-798071_measure_weight_FORCE_MEASUREMENT_CASE.json
✅ Saved cleaned file to All measurements, cleaned\2025-06-15_11-44-43-798071_measure_weight_FORCE_MEASUREMENT_CASE_cleaned.csv

Processing: all measurements\2025-06-15_11-45-14-855432_measure_weight_FORCE_MEASUREMENT_CASE.json
✅ Saved cleaned file to All measurements, cleaned\2025-06-15_11-45-14-855432_measure_weight_FORCE_MEASUREMENT_CASE_cleaned.csv

Processing: all measurements\2025-06-15_11-45-24-472373_measure_weight_FORCE_MEASUREMENT_CASE.json
✅ Saved cleaned file to All measurements, cleaned\2025-06-15_11-45-24-472373_measure_weight_FORCE_MEASUREMENT_CASE_cleaned.csv

Processing: all measurements\2025-06-15_11-48-35-226293_measure_weight_FORCE_MEASUREMENT_CA